# Libraries

In [1]:
import pandas as pd 
import matplotlib.pyplot as plt

# Read data

## genome-scores.csv

In [2]:
genome_scores = pd.read_csv("movies-database/ml-25m/genome-scores.csv")
genome_scores.head()

movieId  tagId  relevance
0        1      1    0.02875
1        1      2    0.02375
2        1      3    0.06250
3        1      4    0.07575
4        1      5    0.14075

In [3]:
genome_scores.count()

movieId      15584448
tagId        15584448
relevance    15584448
dtype: int64

In [4]:
genome_scores[genome_scores["movieId"] == 1]

movieId  tagId  relevance
0           1      1    0.02875
1           1      2    0.02375
2           1      3    0.06250
3           1      4    0.07575
4           1      5    0.14075
...       ...    ...        ...
1123        1   1124    0.05775
1124        1   1125    0.03900
1125        1   1126    0.02975
1126        1   1127    0.08475
1127        1   1128    0.02200

[1128 rows x 3 columns]

## genome-tags.csv

In [5]:
genome_tags = pd.read_csv("movies-database/ml-25m/genome-tags.csv")
genome_tags.head()

tagId           tag
0      1           007
1      2  007 (series)
2      3  18th century
3      4         1920s
4      5         1930s

In [6]:
genome_tags.count()

tagId    1128
tag      1128
dtype: int64

Each movie has 1128 tags ("the tag genome encodes how strongly movies exhibit particular properties represented by tags (atmospheric, thought-provoking, realistic, etc.). The tag genome was computed using a machine learning algorithm on user-contributed content including tags, ratings, and textual reviews") assigned, with a score, which shows how relevant is a specific tag for a movie.

## links.csv

In [7]:
links = pd.read_csv("movies-database/ml-25m/links.csv")
links.count()

movieId    62423
imdbId     62423
tmdbId     62316
dtype: int64

In [8]:
len(genome_scores)/1128 # 1128 - amount of tags permovie

13816.0

not all movies from links.csv have genome scores

## movies.csv

In [9]:
movies = pd.read_csv("movies-database/ml-25m/movies.csv")
movies.head()

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy

In [10]:
movies.count()

movieId    62423
title      62423
genres     62423
dtype: int64

## ratings.csv

In [11]:
ratings = pd.read_csv("movies-database/ml-25m/ratings.csv")
ratings.head()

userId  movieId  rating   timestamp
0       1      296     5.0  1147880044
1       1      306     3.5  1147868817
2       1      307     5.0  1147868828
3       1      665     5.0  1147878820
4       1      899     3.5  1147868510

In [12]:
ratings["movieId"].nunique()

59047

some movies do not have any rating scores

## tags.csv

"Each line of this file after the header row represents one tag applied to one movie by one user"

In [13]:
tags = pd.read_csv("movies-database/ml-25m/tags.csv")
tags.head()

userId  movieId               tag   timestamp
0       3      260           classic  1439472355
1       3      260            sci-fi  1439472256
2       4     1732       dark comedy  1573943598
3       4     1732    great dialogue  1573943604
4       4     7569  so bad it's good  1573943455

In [14]:
tags["movieId"].nunique()

45251

some movies do not have any user-assigned tags

In [15]:
links


movieId   imdbId    tmdbId
0            1   114709     862.0
1            2   113497    8844.0
2            3   113228   15602.0
3            4   114885   31357.0
4            5   113041   11862.0
...        ...      ...       ...
62418   209157  6671244  499546.0
62419   209159   297986   63407.0
62420   209163  6755366  553036.0
62421   209169   249603  162892.0
62422   209171    55323   79513.0

[62423 rows x 3 columns]

I applied for imdb api, while waiting for their reply will use tmdb api

# Merge Data

## Add tmdbid to movies

In [16]:
len(links[links['movieId'].isin(movies['movieId'])])

62423

links and movies dataframes have exactly the same movieIds

In [17]:
movies = pd.merge(movies, links, on='movieId', how='left')
movies.head()

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  imdbId   tmdbId  
0  Adventure|Animation|Children|Comedy|Fantasy  114709    862.0  
1                   Adventure|Children|Fantasy  113497   8844.0  
2                               Comedy|Romance  113228  15602.0  
3                         Comedy|Drama|Romance  114885  31357.0  
4                                       Comedy  113041  11862.0

In [18]:
movies[movies['tmdbId'].isna()]

movieId                                              title  \
706        721           Halfmoon (Paul Bowles - Halbmond) (1995)   
715        730                                    Low Life (1994)   
754        770                                 Costa Brava (1946)   
775        791  Last Klezmer: Leopold Kozlowski, His Life and ...   
1080      1107                                       Loser (1991)   
...        ...                                                ...   
60459   203368                                 The Accused (2018)   
60681   203881                      Aziz Ansari: RIGHT NOW (2019)   
61576   206282                    Rocca verändert die Welt (2019)   
62339   208799                                        Head (2015)   
62343   208806                       First Man on the Moon (2012)   

              genres    imdbId  tmdbId  
706            Drama    114103     NaN  
715            Drama    125877     NaN  
754            Drama     38426     NaN  
775      Documentary    113610     NaN  
1080          Comedy    102336     NaN  
...              ...       ...     ...  
60459       Thriller   7952000     NaN  
60681         Comedy  10575038     NaN  
61576       Children   8773020     NaN  
62339  Comedy|Horror   4035866     NaN  
62343    Documentary   2625082     NaN  

[107 rows x 5 columns]

107 films does not have tmdbid => use imdbid to get tmdbid

In [19]:
# adapt imdbid to an appropriate format
movies['imdb_id_str'] = movies['imdbId'].apply(lambda x: f"tt{int(x):07d}")

In [20]:
from dotenv import load_dotenv
import os

load_dotenv()  

api_key = os.getenv("API_KEY")
auth_token = os.getenv("AUTH_TOKEN")


In [21]:
import requests

headers = {
    "accept": "application/json",
    "Authorization": f"Bearer {auth_token}"
}

def get_tmdb_id(imdb_id_str):
    url = f"https://api.themoviedb.org/3/find/{imdb_id_str}?external_source=imdb_id"
    try:
        response = requests.get(url, headers=headers)
        data = response.json()
        if data['movie_results']:
            return data['movie_results'][0]['id']
    except:
        pass
    return None

mask = movies['tmdbId'].isna()

movies.loc[mask,'tmdbId'] = movies.loc[mask,'imdb_id_str'].apply(get_tmdb_id)
movies['tmdbId'] = movies['tmdbId'].astype('Int64')  # allows for NaNs
movies.head()

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  imdbId  tmdbId imdb_id_str  
0  Adventure|Animation|Children|Comedy|Fantasy  114709     862   tt0114709  
1                   Adventure|Children|Fantasy  113497    8844   tt0113497  
2                               Comedy|Romance  113228   15602   tt0113228  
3                         Comedy|Drama|Romance  114885   31357   tt0114885  
4                                       Comedy  113041   11862   tt0113041

## Add ratings to movies

In [22]:
movie_ratings_dict = ratings.groupby('movieId').apply(
    lambda df: dict(zip(df['userId'], df['rating']))
).reset_index(name='ratings')

# Merge into the movies DataFrame
movies = pd.merge(movies, movie_ratings_dict, on='movieId', how='left')
movies.head()

/tmp/ipykernel_5596/3547453732.py:1: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  movie_ratings_dict = ratings.groupby('movieId').apply(


movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  imdbId  tmdbId imdb_id_str  \
0  Adventure|Animation|Children|Comedy|Fantasy  114709     862   tt0114709   
1                   Adventure|Children|Fantasy  113497    8844   tt0113497   
2                               Comedy|Romance  113228   15602   tt0113228   
3                         Comedy|Drama|Romance  114885   31357   tt0114885   
4                                       Comedy  113041   11862   tt0113041   

                                             ratings  
0  {2: 3.5, 3: 4.0, 4: 3.0, 5: 4.0, 8: 4.0, 10: 3...  
1  {9: 5.0, 12: 2.0, 19: 3.5, 20: 2.5, 35: 3.0, 4...  
2  {8: 4.0, 12: 2.0, 18: 1.5, 23: 5.0, 48: 1.0, 5...  
3  {141: 3.0, 175: 3.0, 230: 3.0, 236: 4.0, 484: ...  
4  {18: 4.0, 48: 3.0, 61: 3.0, 75: 4.0, 77: 3.0, ...

## Add tags to movies

In [23]:
# Group tags by movieId and collect them into lists
movie_tags = tags.groupby('movieId')['tag'].apply(list).reset_index(name='tags')

# Merge into your existing movies_with_ratings DataFrame
movies = pd.merge(movies, movie_tags, on='movieId', how='left')

movies.head()

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  imdbId  tmdbId imdb_id_str  \
0  Adventure|Animation|Children|Comedy|Fantasy  114709     862   tt0114709   
1                   Adventure|Children|Fantasy  113497    8844   tt0113497   
2                               Comedy|Romance  113228   15602   tt0113228   
3                         Comedy|Drama|Romance  114885   31357   tt0114885   
4                                       Comedy  113041   11862   tt0113041   

                                             ratings  \
0  {2: 3.5, 3: 4.0, 4: 3.0, 5: 4.0, 8: 4.0, 10: 3...   
1  {9: 5.0, 12: 2.0, 19: 3.5, 20: 2.5, 35: 3.0, 4...   
2  {8: 4.0, 12: 2.0, 18: 1.5, 23: 5.0, 48: 1.0, 5...   
3  {141: 3.0, 175: 3.0, 230: 3.0, 236: 4.0, 484: ...   
4  {18: 4.0, 48: 3.0, 61: 3.0, 75: 4.0, 77: 3.0, ...   

                                                tags  
0  [Owned, imdb top 250, Pixar, Pixar, time trave...  
1  [Robin Williams, time travel, fantasy, based o...  
2  [funny, best friend, duringcreditsstinger, fis...  
3  [based on novel or book, chick flick, divorce,...  
4  [aging, baby, confidence, contraception, daugh...

In [26]:
import json

movies['ratings'] = movies['ratings'].apply(
    lambda d: json.dumps({str(k): v for k, v in d.items()}) if isinstance(d, dict) else ''
)

movies['tags'] = movies['tags'].apply(
    lambda tags: json.dumps(tags) if isinstance(tags, list) else ''
)

movies.head()


movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  imdbId  tmdbId imdb_id_str  \
0  Adventure|Animation|Children|Comedy|Fantasy  114709     862   tt0114709   
1                   Adventure|Children|Fantasy  113497    8844   tt0113497   
2                               Comedy|Romance  113228   15602   tt0113228   
3                         Comedy|Drama|Romance  114885   31357   tt0114885   
4                                       Comedy  113041   11862   tt0113041   

                                             ratings  \
0  {"2": 3.5, "3": 4.0, "4": 3.0, "5": 4.0, "8": ...   
1  {"9": 5.0, "12": 2.0, "19": 3.5, "20": 2.5, "3...   
2  {"8": 4.0, "12": 2.0, "18": 1.5, "23": 5.0, "4...   
3  {"141": 3.0, "175": 3.0, "230": 3.0, "236": 4....   
4  {"18": 4.0, "48": 3.0, "61": 3.0, "75": 4.0, "...   

                                                tags  
0  ["Owned", "imdb top 250", "Pixar", "Pixar", "t...  
1  ["Robin Williams", "time travel", "fantasy", "...  
2  ["funny", "best friend", "duringcreditsstinger...  
3  ["based on novel or book", "chick flick", "div...  
4  ["aging", "baby", "confidence", "contraception...

In [ ]:
movies.to_csv("movies_combined.csv", index=False)